In [2]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load in 

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the "../input/" directory.
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# Any results you write to the current directory are saved as output.

In [3]:
import numpy as np 
import pandas as pd 
import os

import tensorflow as tf
from sklearn.feature_extraction.text import CountVectorizer
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
from keras.models import Model
from keras.callbacks import EarlyStopping,ModelCheckpoint,ReduceLROnPlateau


from keras.layers import Dense, Embedding, LSTM, Input, Lambda
from sklearn.model_selection import train_test_split
# from keras.utils.np_utils import to_categorical # Not working!
from keras.utils import to_categorical # Instead use this one~

import keras.backend as K
from keras.optimizers import Adadelta
import re

In [5]:
data = pd.read_csv('./train.csv')
pd.set_option('display.max_colwidth',None)
data.head()

ID  \
0   0   
1   1   
2   2   
3   3   
4   4   

                                                                                                                                                           Sentence1  \
0                                                                                 But instead of returning to heaven , Annie decided to join Chris in hell forever .   
1  In 2016 , Bacardi announced new branding and plans to sell their version of Havana Club nationally , which will be burned in Florida and bottled in Puerto Rico .   
2                                    Kweku Baako Jnr had four children . One of them , Baako is a journalist and editor of the `` New Crusading Guide '' newspaper .   
3             As with the Navy , the Army has a single-track system , where officers from other Navy communities transfer over to Foreign Area Officer permanently .   
4                                                                          Sissi units have fewer crew served weapons and more sniper rifles than regular infantry .   

                                                                                                                                                              Sentence2  \
0                                                                                    But instead of returning to Heaven , Chris chooses to join Annie forever in Hell .   
1  In 2016 , Bacardi announced new branding and plans to sell their version of Havana Club nationally , which will be distilled in Puerto Rico and bottled in Florida .   
2                                      Baako had four children , one of whom was Kweku Baako Jnr , a journalist and editor of the newspaper `` New Crusading Guide '' .   
3                        Like the army , the Navy has a single-track system , where officers from other Navy communities permanently transfer to Foreign Area Officer .   
4                                                                      Sissi units have more weapons served by the crew and fewer sniper rifles than regular infantry .   

   Class  
0      0  
1      0  
2      0  
3      0  
4      0

In [6]:
df = pd.read_csv('./test.csv')
pd.set_option('display.max_colwidth',None)
df.head()

ID  \
0  16000   
1  16001   
2  16002   
3  16003   
4  16004   

                                                                                                                                                  Sentence1  \
0                                                                                                          How do I increase the rank on my website in SEO?   
1                                                                                                I'm a boy. I masturbate. I'm 13. Is it bad to masturbate?    
2                              The fourth season was premiered on 7 June 2010 , and like the third season was the system of competition for mixed couples .   
3                                      In 2003 , he moved to London and lived there for sixteen months before returning to South Africa in September 2004 .   
4  Shawn told Shawn that his mother was not dead and his father was still married and on the day of the wedding of Colleen and Santo , Shawn told Colleen .   

                                                                                                                                                Sentence2  
0                                                                                           What are some tips on how to increase rank in search engines?  
1                                                                                                                  Why do I masturbate when I'm stressed?  
2                           The third season was premiered on June 7 , 2010 . Like the fourth season the system of the competition was in mixed couples .  
3                                               He moved to South Africa in 2003 and lived there 16 months before returning to London in September 2004 .  
4  Stefano told Shawn that his mother was not dead and his father was still married and on the day of Colleen and Santo 's wedding , Shawn told Colleen .

In [7]:
data.shape

(16000, 4)

In [8]:
data

ID  \
0          0   
1          1   
2          2   
3          3   
4          4   
...      ...   
15995  15995   
15996  15996   
15997  15997   
15998  15998   
15999  15999   

                                                                                                                                                               Sentence1  \
0                                                                                     But instead of returning to heaven , Annie decided to join Chris in hell forever .   
1      In 2016 , Bacardi announced new branding and plans to sell their version of Havana Club nationally , which will be burned in Florida and bottled in Puerto Rico .   
2                                        Kweku Baako Jnr had four children . One of them , Baako is a journalist and editor of the `` New Crusading Guide '' newspaper .   
3                 As with the Navy , the Army has a single-track system , where officers from other Navy communities transfer over to Foreign Area Officer permanently .   
4                                                                              Sissi units have fewer crew served weapons and more sniper rifles than regular infantry .   
...                                                                                                                                                                  ...   
15995    On July 21st , 1919 , the army was renamed into the Crimean Rifle Division which in six days was dissolved and transformed again into the 58th Rifle Division .   
15996                                     In 2012 , the championships were held in Dunakeszi , Hungary , in 2013 in Pouch , Germany , and in 2014 in Luserna ( Italy ) .   
15997                                                                                              At least 3 inserts were printed , but none of them were anticipated .   
15998                     The builders of Waimate North were also William William Cook and the son of St. James , who in 1871 built the Church of St. John the Baptist .   
15999                                                                                     It was destroyed and finally rebuilt during the Manchester lightning in 1940 .   

                                                                                                                                                                  Sentence2  \
0                                                                                        But instead of returning to Heaven , Chris chooses to join Annie forever in Hell .   
1      In 2016 , Bacardi announced new branding and plans to sell their version of Havana Club nationally , which will be distilled in Puerto Rico and bottled in Florida .   
2                                          Baako had four children , one of whom was Kweku Baako Jnr , a journalist and editor of the newspaper `` New Crusading Guide '' .   
3                            Like the army , the Navy has a single-track system , where officers from other Navy communities permanently transfer to Foreign Area Officer .   
4                                                                          Sissi units have more weapons served by the crew and fewer sniper rifles than regular infantry .   
...                                                                                                                                                                     ...   
15995                 On July 21 , 1919 , the army was renamed the Crimean Rifle Division , which was dissolved in six days and turned into the 58th Rifle Division again .   
15996                                        In 2012 , the championships were held in Italy , in Pouch , Germany in 2013 , and in 2014 in Dunakeszi , Hungary ( Luserna ) .   
15997                                                                                             At least 3 supplements were printed , but none of them were anticipated .   
15

In [9]:
train_1 = data.iloc[:,1]
train_1 = list(train_1)
print(train_1)

['But instead of returning to heaven , Annie decided to join Chris in hell forever .', 'In 2016 , Bacardi announced new branding and plans to sell their version of Havana Club nationally , which will be burned in Florida and bottled in Puerto Rico .', "Kweku Baako Jnr had four children . One of them , Baako is a journalist and editor of the `` New Crusading Guide '' newspaper .", 'As with the Navy , the Army has a single-track system , where officers from other Navy communities transfer over to Foreign Area Officer permanently .', 'Sissi units have fewer crew served weapons and more sniper rifles than regular infantry .', 'However , the United States later forced other nations and American companies to restrict trade with Cuba with foreign subsidiaries .', 'Deutsche Bahn opened a new underground tunnel to the new railway station Filderstadt on 29 September 2001 .', 'Some Hebrew and Aramaic abbreviations may not be included here ; more may be found in the List of Hebrew abbreviations an

In [10]:
train_2 = data.iloc[:,2]
train_2 = list(train_2)
print(train_2)

['But instead of returning to Heaven , Chris chooses to join Annie forever in Hell .', 'In 2016 , Bacardi announced new branding and plans to sell their version of Havana Club nationally , which will be distilled in Puerto Rico and bottled in Florida .', "Baako had four children , one of whom was Kweku Baako Jnr , a journalist and editor of the newspaper `` New Crusading Guide '' .", 'Like the army , the Navy has a single-track system , where officers from other Navy communities permanently transfer to Foreign Area Officer .', 'Sissi units have more weapons served by the crew and fewer sniper rifles than regular infantry .', 'However , the United States later pressured other nations and foreign companies with American subsidiaries to restrict trade with Cuba .', 'On 29 September 2001 , Deutsche Bahn opened a new tunnel to the new Filderstadt U-Bahn ( underground ) station .', 'Some Hebrew and Aramaic abbreviations may not be included here , and others may be found in the list of Hebrew

In [11]:
full_train = train_1 + train_2
print(full_train)

['But instead of returning to heaven , Annie decided to join Chris in hell forever .', 'In 2016 , Bacardi announced new branding and plans to sell their version of Havana Club nationally , which will be burned in Florida and bottled in Puerto Rico .', "Kweku Baako Jnr had four children . One of them , Baako is a journalist and editor of the `` New Crusading Guide '' newspaper .", 'As with the Navy , the Army has a single-track system , where officers from other Navy communities transfer over to Foreign Area Officer permanently .', 'Sissi units have fewer crew served weapons and more sniper rifles than regular infantry .', 'However , the United States later forced other nations and American companies to restrict trade with Cuba with foreign subsidiaries .', 'Deutsche Bahn opened a new underground tunnel to the new railway station Filderstadt on 29 September 2001 .', 'Some Hebrew and Aramaic abbreviations may not be included here ; more may be found in the List of Hebrew abbreviations an

In [12]:
num_words = 5000
tokenizer = Tokenizer(num_words=num_words, filters='!"#$%&()*+,-./:;<=>?@[\\]^_`{|}~\t\n',
                                   lower=True,split=' ')


In [13]:
tokenizer.fit_on_texts(full_train)
word_index = tokenizer.word_index
print('Found %s unique tokens.' % len(word_index))
print(word_index)

Found 29965 unique tokens.
{'the': 1, 'in': 2, 'and': 3, 'of': 4, 'a': 5, 'is': 6, 'to': 7, 'was': 8, 'by': 9, 'on': 10, 'for': 11, 'with': 12, 'as': 13, 'he': 14, "''": 15, 'from': 16, 'it': 17, 'are': 18, 'his': 19, 'at': 20, 'that': 21, 'new': 22, 'were': 23, 'what': 24, 'an': 25, 'first': 26, 'also': 27, 'born': 28, 'has': 29, "'s": 30, 'i': 31, 'or': 32, 'river': 33, 'which': 34, 'be': 35, 'how': 36, 'this': 37, 'who': 38, 'can': 39, 'after': 40, '\r': 41, '6': 42, 'but': 43, 'do': 44, 'had': 45, 'county': 46, 'north': 47, 'city': 48, 'district': 49, 'south': 50, 'two': 51, 'when': 52, 'one': 53, 'have': 54, '1': 55, 'she': 56, 'located': 57, 'season': 58, 'they': 59, 'married': 60, 'its': 61, 'not': 62, 'school': 63, 'state': 64, 'second': 65, 'her': 66, 'said': 67, 'there': 68, '2': 69, 'son': 70, 'between': 71, 'family': 72, 'their': 73, '4': 74, 'john': 75, 'where': 76, 'other': 77, '3': 78, 'died': 79, 'later': 80, 'national': 81, 'then': 82, 'won': 83, 'played': 84, 'you': 8

In [14]:
X_1 = tokenizer.texts_to_sequences(data['Sentence1'].values)
print(X_1[0])
maxlen = 60
X_1 = pad_sequences(X_1, maxlen=maxlen)
print("Padded Sequences: ")
print(X_1)
print(X_1[0])

[43, 601, 4, 2280, 7, 2339, 1891, 7, 2018, 557, 2, 4211]
Padded Sequences: 
[[   0    0    0 ...  557    2 4211]
 [   0    0    0 ...    2 1656 2340]
 [   0    0    0 ...   22   15  882]
 ...
 [   0    0    0 ...    4  287   23]
 [   0    0    0 ...  364   75    1]
 [   0    0    0 ... 1035    2 1074]]
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0   43  601    4 2280    7 2339 1891    7
 2018  557    2 4211]


In [15]:
X_1.shape

(16000, 60)

In [16]:
X_2 = tokenizer.texts_to_sequences(data['Sentence2'].values)
print(X_2[0])
maxlen = 60
X_2 = pad_sequences(X_2, maxlen=maxlen)
print("Padded Sequences: ")
print(X_2)
print(X_2[0])

[43, 601, 4, 2280, 7, 557, 7, 2018, 2339, 4211, 2]
Padded Sequences: 
[[   0    0    0 ... 2339 4211    2]
 [   0    0    0 ...    3    2  463]
 [   0    0    0 ...  882   22   15]
 ...
 [   0    0    0 ...    4  287   23]
 [   0    0    0 ...  364   75    1]
 [   0    0    0 ... 1035    2 1074]]
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0   43  601    4 2280    7  557    7
 2018 2339 4211    2]


In [17]:
X_2.shape

(16000, 60)

In [18]:
training_portion = 0.8
y = list(data.iloc[:,3])

In [19]:
X_t1 = tokenizer.texts_to_sequences(df['Sentence1'].values)
print(X_t1[0])
maxlen = 60
X_t1 = pad_sequences(X_t1, maxlen=maxlen)
print("Padded Sequences: ")
print(X_t1)
print(X_t1[0])

[36, 44, 31, 852, 1, 1694, 10, 139, 1733, 2]
Padded Sequences: 
[[   0    0    0 ...  139 1733    2]
 [   0    0    0 ...   17 1098    7]
 [   0    0    0 ...  989   11 1292]
 ...
 [   0    0    0 ...   22   87   48]
 [   0    0    0 ...  552   23  104]
 [   0    0    0 ...    8 2005    7]]
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0   36   44   31  852    1 1694
   10  139 1733    2]


In [20]:
X_t1.shape

(4700, 60)

In [21]:
X_t2 = tokenizer.texts_to_sequences(df['Sentence2'].values)
print(X_t2[0])
maxlen = 60
X_t2 = pad_sequences(X_t2, maxlen=maxlen)
print("Padded Sequences: ")
print(X_t2)
print(X_t2[0])

[24, 18, 89, 10, 36, 7, 852, 1694, 2, 2306]
Padded Sequences: 
[[   0    0    0 ... 1694    2 2306]
 [   0    0    0 ...   31   52 2430]
 [   0    0    0 ...    8    2 1292]
 ...
 [   0    0    0 ...   48    2  210]
 [   0    0    0 ...   10   81  552]
 [   0    0    0 ... 2005    7 2207]]
[   0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0    0    0    0    0    0    0
    0    0    0    0    0    0    0    0   24   18   89   10   36    7
  852 1694    2 2306]


In [22]:
X_t2.shape

(4700, 60)

In [23]:
training_size = int(len(X_1)*training_portion)

X_train1 = X_1[:training_size,:]
X_train2 = X_2[:training_size,:]
y_train  = y[:training_size]
X_val1   = X_1[training_size:,:]
X_val2   = X_2[training_size:,:]
y_val    = y[training_size:]


In [24]:
X_train1.shape
X_train2.shape
len(y_train)

12800

In [52]:
embedding_dim = 40 #Change to observe effects
lstm_out = 256
gradient_clipping_norm = 2.50
batch_size = 128
n_epoch = 5


In [53]:
reduce_lr = ReduceLROnPlateau(monitor='val_loss', factor=0.2,
                              patience=5, min_lr=0.001)

earlystop = EarlyStopping(monitor='val_loss', mode='min', verbose=1, patience=5)

modelcheckpoint = ModelCheckpoint("weights.{epoch:02d}-{val_loss:.2f}.h5", monitor='val_loss', verbose=0, save_best_only=True, save_weights_only=False, mode='auto',  save_freq='epoch')

callbacks = [earlystop,modelcheckpoint,reduce_lr]

In [54]:
def exponent_neg_manhattan_distance(left, right):
    ''' Helper function for the similarity estimate of the LSTMs outputs'''
    return K.exp(-K.sum(K.abs(left-right), axis=1, keepdims=True))



left_input = Input(shape=(maxlen,), dtype='int32')
right_input = Input(shape=(maxlen,), dtype='int32')

embedding_layer = Embedding(num_words, embedding_dim, input_length=maxlen, trainable=False)

# Embedded version of the inputs
encoded_left = embedding_layer(left_input)
encoded_right = embedding_layer(right_input)

# Since this is a siamese network, both sides share the same LSTM
shared_lstm = LSTM(lstm_out)

left_output = shared_lstm(encoded_left)
right_output = shared_lstm(encoded_right)

malstm_distance = Lambda(function=lambda x: exponent_neg_manhattan_distance(x[0], x[1]),output_shape=lambda x: (x[0][0], 1))([left_output, right_output])


malstm = Model([left_input, right_input], [malstm_distance])

# Adadelta optimizer, with gradient clipping by norm
optimizer = Adadelta(clipnorm=gradient_clipping_norm,learning_rate=1.0,rho=0.95)

malstm.compile(loss='mean_squared_error', optimizer=optimizer, metrics=['accuracy'])

# Use tf.compat.v1.executing_eagerly_outside_functions instead of tf.executing_eagerly_outside_functions
# tf.compat.v1.executing_eagerly_outside_functions

print(malstm.summary())

 

Model: "model_2"
__________________________________________________________________________________________________
 Layer (type)                Output Shape                 Param #   Connected to                  
 input_5 (InputLayer)        [(None, 60)]                 0         []                            
                                                                                                  
 input_6 (InputLayer)        [(None, 60)]                 0         []                            
                                                                                                  
 embedding_2 (Embedding)     (None, 60, 40)               200000    ['input_5[0][0]',             
                                                                     'input_6[0][0]']             
                                                                                                  
 lstm_2 (LSTM)               (None, 256)                  304128    ['embedding_2[0][0]',   

In [55]:



malstm_trained = malstm.fit([X_train1, X_train2], np.array(y_train), batch_size=batch_size, epochs=n_epoch,
                            validation_data=([X_val1, X_val2], np.array(y_val)), callbacks=callbacks)

Epoch 1/5
100/100 [==============================] - 26s 237ms/step - loss: 0.2805 - accuracy: 0.5294 - val_loss: 0.2643 - val_accuracy: 0.5663 - lr: 1.0000
Epoch 2/5


c:\Users\Gizaw\AppData\Local\Programs\Python\Python311\Lib\site-packages\keras\src\engine\training.py:3103: UserWarning: You are saving your model as an HDF5 file via `model.save()`. This file format is considered legacy. We recommend using instead the native Keras format, e.g. `model.save('my_model.keras')`.
  saving_api.save_model(


100/100 [==============================] - 23s 233ms/step - loss: 0.2592 - accuracy: 0.5703 - val_loss: 0.2491 - val_accuracy: 0.5950 - lr: 1.0000
Epoch 3/5
100/100 [==============================] - 25s 252ms/step - loss: 0.2445 - accuracy: 0.6047 - val_loss: 0.2366 - val_accuracy: 0.6244 - lr: 1.0000
Epoch 4/5
100/100 [==============================] - 26s 261ms/step - loss: 0.2359 - accuracy: 0.6274 - val_loss: 0.2330 - val_accuracy: 0.6338 - lr: 1.0000
Epoch 5/5
100/100 [==============================] - 25s 255ms/step - loss: 0.2318 - accuracy: 0.6384 - val_loss: 0.2318 - val_accuracy: 0.6381 - lr: 1.0000


In [32]:
malstm.load_weights("weights.01-0.26.h5")
print("Loaded model from disk")

Loaded model from disk


In [33]:
loss = malstm.evaluate([X_val1,X_val2], np.array(y_val), batch_size = batch_size, callbacks=[earlystop])
print(loss)

25/25 [==============================] - 2s 67ms/step - loss: 0.2640 - accuracy: 0.5703
[0.26399433612823486, 0.5703125]


In [34]:
y_pred = malstm.predict([X_t1,X_t2])

147/147 [==============================] - 4s 25ms/step


In [ ]:
# check
print(malstm)

In [36]:
y_pred

array([[0.4168897 ],
       [0.17260471],
       [0.34780568],
       ...,
       [0.46894485],
       [0.4472736 ],
       [0.50463265]], dtype=float32)

In [38]:
y_out = y_pred>0.5

In [39]:
y_out

array([[False],
       [False],
       [False],
       ...,
       [False],
       [False],
       [ True]])

In [40]:
y_out = []
for i in range(len(y_pred)):
    val = y_pred[i]
    if val >= 0.5:
        y_out.append(1)
    else:
        y_out.append(0)

In [41]:
y_out

[0,
 0,
 0,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 0,
 1,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 1,
 1,
 0,
 0,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 0,
 1,
 1,
 1,
 1,
 0,
 0,
 1,
 1,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 0,
 0,
 0,
 1,
 0,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 1,
 1,
 0,
 0,
 0,
 0,
 1,
 0,
 1,
 0,
 1,
 1,
 0,
 0,
 0,
 1,
 1,
 0,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 0,
 0,
 1,
 1,
 0,
 1,
 1,
 1,
 0,
 1,
 0,
 1,
 1,
 0,
 1,
 1,
 0,
 1,
 1,
 1,
 1,
 1,
 0,
 0,
 1,
 1,
 1,
 1,
 0,
 0,
 0,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 0,
 0,
 1,
 0,
 1,
 0,
 1,
 1,
 1,
 0,
 1,
 1,
 1,
 0,
 1,
 1,
 0,
 0,
 0,
 1,
 1,
 1,
 1,
 0,
 0,
 1,
 1,
 1,
 1,
 1,
 0,
 1,
 1,
 0,
 0,
 0,
 1,
 1,
 0,
 1,
 0,
 1,
 1,
 0,
 0,
 1,
 1,
 0,
 1,
 1,


In [42]:
np.max(y_pred)

1.0

In [43]:
np.min(y_pred)

0.014283414

In [44]:

len(y_pred)

4700

In [45]:
df.shape

(4700, 3)

In [46]:



df['Class'] = y_out

In [47]:
df_2 = df[['ID', 'Class']]

In [48]:




df_2.index = df_2.index + 1

In [49]:
df_2.to_csv("submission_1.csv",index=False)

In [50]:
df_2.head()

ID  Class
1  16000      0
2  16001      0
3  16002      0
4  16003      1
5  16004      1

In [71]:
from IPython.display import HTML
import pandas as pd
import numpy as np
import base64
def create_download_link(df, title = "Download CSV file", filename = "data.csv"):
  csv = df.to_csv(index=False)
  b64 = base64.b64encode(csv.encode())
  payload = b64.decode()
  html = '<a download="{filename}" href="data:text/csv;base64,{payload}"target="_blank">{title}</a>'
  html = html.format(payload=payload,title=title,filename=filename)
  return HTML(html)
create_download_link(df_2)